In [1]:
# load package
import os
import time
import datetime
import calendar
import json
import pandas as pd
import numpy as np
import scipy.stats as stats
import matplotlib.pyplot as plt
import joblib
import pickle
# load sklearn
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report
from sklearn.metrics import confusion_matrix
from sklearn.linear_model import LinearRegression
from sklearn.svm import SVC, SVR
from sklearn_rvm import EMRVC
from sklearn_rvm import EMRVR
from sklearn.multioutput import MultiOutputClassifier
from sklearn.multioutput import MultiOutputRegressor
from sklearn.preprocessing import MinMaxScaler

import xgboost as xgb
import lightgbm as lgb
## 在線使用設置##############
import plotly as py
import plotly.graph_objs as go
from plotly.offline import iplot, init_notebook_mode
import plotly.express as px
import cufflinks as cf
cf.go_offline()
cf.set_config_file(offline=False, world_readable=True)

In [2]:
# linear interpolation 線性插值
from scipy.interpolate import interp1d
def interpolate(x, kind='linear'):
    not_nan = np.logical_not(np.isnan(x))
    indices = np.arange(len(x))
#     interp = interp1d(indices[not_nan], x[not_nan], kind=kind)
    interp = interp1d(indices[not_nan], x[not_nan], kind=kind,fill_value="extrapolate")
    return interp(indices)

In [3]:
# Metrics
def MAPE(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100
#mre=nmape
def MRE(y_true, y_pred, capacity):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs((y_true - y_pred))/capacity) * 100

def nMAE(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs(y_true - y_pred))/y_true.mean() * 100

def MAE(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs(y_true - y_pred))

def RMSE(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.sqrt(((y_pred - y_true) ** 2).mean())

def nRMSE(y_true, y_pred):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.sqrt(((y_pred - y_true) ** 2).mean())/y_true.mean()*100

def cRMSE(y_true, y_pred, capacity):
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.sqrt(((y_pred - y_true) ** 2).mean())/capacity*100

In [4]:
def model_build(train_x, train_y, train_idx, test_x, test_y, test_idx, model_name):
    #模型訓練
    if model_name == 'xgb':
        model = xgb.XGBRegressor(objective='reg:squarederror',
                        learning_rate=0.01, 
                        max_depth=1,
                        colsample_bytree=0.1,
                        reg_lambda=0.01,
                        seed=1,
                        subsample=0.1,
                        min_child_weight=1,
                        n_estimators=4000).fit(train_x, train_y)
    elif model_name == 'lgb':
        model = lgb.LGBMRegressor(
               boosting_type='gbdt',
                     verbose = 0,
                     learning_rate = 0.01,
                     num_leaves = 35,
                     feature_fraction=0.8,
                     bagging_fraction= 0.9,
                     bagging_freq= 8,
                     lambda_l1= 0.6,
                     lambda_l2= 0).fit(train_x, train_y)
    elif model_name == 'svr':
        model = SVR(C=1, kernel="rbf", gamma='auto').fit(train_x, train_y)
    elif model_name == 'rvm':
        model = EMRVR(kernel="rbf", gamma='auto')
        model.fit(train_x, train_y)
#         joblib.dump(model,'./model/1D_power/6-17/2022_rvm_CWB_pred_d.pkl')
    elif model_name == 'persistence':
        test_x = scaler_x.inverse_transform(test_x)
        test_x = test_x.reshape(-1)
        test_y = test_y.reshape(-1)
        test_idx['pred'] = test_x
        test_idx['true'] = test_y
        return test_idx



#     other_params = {'learning_rate': 0.1, 'n_estimators': 500, 'max_depth': 5, 'min_child_weight': 1, 'seed': 0,
#     'subsample': 0.8, 'colsample_bytree': 0.8, 'gamma': 0, 'reg_alpha': 0, 'reg_lambda': 1}
#     model = xgb.XGBRegressor(**other_params).fit(train_x, train_y)

# 預測
    pred_y = model.predict(test_x)
    
    
# 反正規劃
    pred_y = pred_y.reshape(-1,1)
    pred_y = scaler_y.inverse_transform(pred_y)
    pred_y = pred_y.reshape(-1)
    test_idx['pred'] = pred_y
    test_idx['true'] = test_y
    return test_idx

In [5]:
merge_raw = pd.read_csv(f'solar_汙水廠(history).csv', low_memory=False)
data = merge_raw.copy()
data = data.drop_duplicates(subset=['TIME_TO_INTERVAL'], keep='last')
data = data.dropna(subset=['Power'])
data['TIME_TO_INTERVAL'] = pd.to_datetime(data['TIME_TO_INTERVAL'])
#抓取>2022年的資料
test_split_date1 = '2022-02-01'
test_split_date2 = '2022-10-31'
test_split_date1 = pd.to_datetime(test_split_date1)
mask_1 = (data['TIME_TO_INTERVAL']>=test_split_date1)
mask_2 = (data['TIME_TO_INTERVAL']<=test_split_date2)
data = data[(mask_1&mask_2)]
data['Hour'] = pd.to_datetime(data['TIME_TO_INTERVAL']).dt.hour
data['Date'] = pd.to_datetime(data['TIME_TO_INTERVAL']).dt.date
data['Date'] = pd.to_datetime(data['Date'])
mask = ((data['Hour']>=6) & (data['Hour']<=17))
data = data[mask]
data = data[['TIME_TO_INTERVAL','Date','Hour','Power']].reset_index(drop=True)
data

TIME_TO_INTERVAL       Date  Hour     Power
0    2022-02-27 06:00:00 2022-02-27     6  0.172272
1    2022-02-27 07:00:00 2022-02-27     7  1.883819
2    2022-02-27 08:00:00 2022-02-27     8  4.012042
3    2022-02-27 09:00:00 2022-02-27     9  5.605072
4    2022-02-27 10:00:00 2022-02-27    10  6.578561
...                  ...        ...   ...       ...
2175 2022-10-30 11:00:00 2022-10-30    11  4.761714
2176 2022-10-30 12:00:00 2022-10-30    12  3.412161
2177 2022-10-30 13:00:00 2022-10-30    13  4.729319
2178 2022-10-30 14:00:00 2022-10-30    14  4.078483
2179 2022-10-30 15:00:00 2022-10-30    15  2.323181

[2180 rows x 4 columns]

In [6]:
cloud_data = pd.read_csv(f'cloud_datas_hour.csv')
cloud_data['TIME_TO_INTERVAL'] = pd.to_datetime(cloud_data['TIME_TO_INTERVAL'])
cloud_data.rename(columns={'TIME_TO_INTERVAL': 'Date', 'time': 'Hour'}, inplace=True)
cloud_data['cloud'] = cloud_data['cloud'].where(cloud_data['cloud'] >= 0, 0)
cloud_data['low'] = cloud_data['low'].where(cloud_data['low'] >= 0, 0)
cloud_data['mid'] = cloud_data['mid'].where(cloud_data['mid'] >= 0, 0)
cloud_data['hig'] = cloud_data['hig'].where(cloud_data['hig'] >= 0, 0)
data = pd.merge(data,cloud_data,on=['Date','Hour'],how='inner')
data

TIME_TO_INTERVAL       Date  Hour     Power      lon     lat  \
0    2022-02-27 06:00:00 2022-02-27     6  0.172272  120.425  23.325   
1    2022-02-27 07:00:00 2022-02-27     7  1.883819  120.725  23.625   
2    2022-02-27 08:00:00 2022-02-27     8  4.012042  121.025  23.925   
3    2022-02-27 09:00:00 2022-02-27     9  5.605072  121.325  24.225   
4    2022-02-27 10:00:00 2022-02-27    10  6.578561  121.625  24.525   
...                  ...        ...   ...       ...      ...     ...   
2175 2022-10-30 11:00:00 2022-10-30    11  4.761714  121.925  24.825   
2176 2022-10-30 12:00:00 2022-10-30    12  3.412161  122.225  25.125   
2177 2022-10-30 13:00:00 2022-10-30    13  4.729319  122.525  25.425   
2178 2022-10-30 14:00:00 2022-10-30    14  4.078483  122.825  25.725   
2179 2022-10-30 15:00:00 2022-10-30    15  2.323181      NaN  25.925   

         cloud       low  mid  hig  
0     0.000000  0.000000  0.0  0.0  
1     0.000000  0.000000  0.0  0.0  
2     0.000000  0.000000  0.0  0.0  
3     5.471000  5.471000  0.0  0.0  
4     7.893267  7.893267  0.0  0.0  
...        ...       ...  ...  ...  
2175  0.000000  0.000000  0.0  0.0  
2176  0.000000  0.000000  0.0  0.0  
2177  0.000000  0.000000  0.0  0.0  
2178  0.000000  0.000000  0.0  0.0  
2179  0.000000  0.000000  0.0  0.0  

[2180 rows x 10 columns]

In [7]:
def Similarity(row_data,data):
    #獲得先前時間
    mask = (data['Date']<row_data['Date'][0])
    pre_data = data[mask]
    #獲得相同時間段
    mask2 = (pre_data['Hour'] == row_data['Hour'][0])
    pre_data_time = pre_data[mask2].reset_index(drop=True)
    #一筆一筆跟該資料做比較
    future = pd.DataFrame()
    similary = pd.DataFrame()
    for i in range(len(pre_data_time)):
        pre_row = pre_data_time.loc[i:i].reset_index(drop=True)
#         sim = distance.euclidean([pre_row['cloud']],[row_data['cloud']])
#         sim = 1 - spatial.distance.cosine([pre_row['cloud']],[row_data['cloud']])
        sim = cosine_similarity([pre_row['cloud']],[row_data['cloud']])
        print(sim)
        if(sim == 1):
#             print(pre_row['cloud'])
#             print(row_data['cloud'])
            similary = pd.concat([similary,pre_row['Power']],axis=0)
    future['cloud_Power'] = similary.mean()
    future['TIME_TO_INTERVAL'] = row_data['TIME_TO_INTERVAL']
    return future

In [8]:
def pre_power(row_data,data):
    pre_power = pd.DataFrame()
    #獲得先前時間
    mask = (data['Date']==row_data['Date'][0]-datetime.timedelta(days=1))
    pre_data = data[mask]
    #獲得相同時間段
    mask2 = (pre_data['Hour'] == row_data['Hour'][0])
    pre_data_time = pre_data[mask2].reset_index(drop=True)
    pre_power['pre_Power'] = pre_data_time['Power']
    pre_power['TIME_TO_INTERVAL'] = row_data['TIME_TO_INTERVAL']
    return pre_power

In [9]:
from scipy.spatial import distance
from scipy import spatial
from sklearn.metrics.pairwise import cosine_similarity
from tqdm import tqdm
future_power = pd.DataFrame()
for i in tqdm(range(len(data))):
    row_data = data.loc[i:i].reset_index(drop=True)
    Similarity_data = Similarity(row_data,data)
    pre_power_data = pre_power(row_data,data)
    merge_data = pd.merge(Similarity_data,pre_power_data,on=['TIME_TO_INTERVAL'],how='inner')
    future_power = pd.concat([future_power,merge_data],axis=0)
future_power.reset_index(drop=True)

  1%|█                                                                              | 28/2180 [00:00<00:16, 134.44it/s]

[[0.]]
[[0.]]
[[0.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[1.]]
[[0.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[1.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[0.]]
[[1.]]
[[0.]]
[[0.]]
[[1.]]

  3%|█▉                                                                             | 55/2180 [00:00<00:19, 110.75it/s]


[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[1.]]
[[1.]]
[[1.]]
[[1.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[1.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[0.]]
[[0.]]
[[1.]]
[[1.]]
[[0.]]
[[0.]]
[[0.]]
[[1.]]
[[0.]]
[[0.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[1.]]
[[0.]]
[[1.]]
[[1.]]
[[1.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]


  3%|██▍                                                                            | 67/2180 [00:00<00:20, 101.97it/s]

...

100%|█████████████████████████████████████████████████████████████████████████████▉| 2179/2180 [04:56<00:00,  4.56it/s]

[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]

100%|██████████████████████████████████████████████████████████████████████████████| 2180/2180 [04:57<00:00,  7.34it/s]

[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]
[[0.]]


cloud_Power    TIME_TO_INTERVAL  pre_Power
0             NaN 2022-02-27 06:00:00        NaN
1             NaN 2022-02-27 07:00:00        NaN
2             NaN 2022-02-27 08:00:00        NaN
3             NaN 2022-02-27 09:00:00        NaN
4             NaN 2022-02-27 10:00:00        NaN
...           ...                 ...        ...
2175          NaN 2022-10-30 11:00:00   6.549119
2176          NaN 2022-10-30 12:00:00   6.413550
2177          NaN 2022-10-30 13:00:00   5.641947
2178          NaN 2022-10-30 14:00:00   3.924533
2179          NaN 2022-10-30 15:00:00   1.794878

[2180 rows x 3 columns]

In [10]:
future_power.head(50)

cloud_Power    TIME_TO_INTERVAL  pre_Power
0          NaN 2022-02-27 06:00:00        NaN
0          NaN 2022-02-27 07:00:00        NaN
0          NaN 2022-02-27 08:00:00        NaN
0          NaN 2022-02-27 09:00:00        NaN
0          NaN 2022-02-27 10:00:00        NaN
0          NaN 2022-02-27 11:00:00        NaN
0          NaN 2022-02-27 12:00:00        NaN
0          NaN 2022-02-27 13:00:00        NaN
0          NaN 2022-02-27 14:00:00        NaN
0          NaN 2022-02-27 15:00:00        NaN
0          NaN 2022-02-27 16:00:00        NaN
0          NaN 2022-02-27 17:00:00        NaN
0          NaN 2022-03-18 06:00:00        NaN
0          NaN 2022-03-18 07:00:00        NaN
0          NaN 2022-03-18 08:00:00        NaN
0     5.605072 2022-03-18 09:00:00        NaN
0     6.578561 2022-03-18 10:00:00        NaN
0          NaN 2022-03-18 11:00:00        NaN
0     7.472419 2022-03-18 12:00:00        NaN
0          NaN 2022-03-18 13:00:00        NaN
0          NaN 2022-03-18 14:00:00        NaN
0          NaN 2022-03-18 15:00:00        NaN
0          NaN 2022-03-18 16:00:00        NaN
0          NaN 2022-03-18 17:00:00        NaN
0          NaN 2022-04-01 15:00:00        NaN
0          NaN 2022-04-01 16:00:00        NaN
0          NaN 2022-04-01 17:00:00        NaN
0     0.164561 2022-04-02 06:00:00        NaN
0     1.751811 2022-04-02 07:00:00        NaN
0     2.900564 2022-04-02 08:00:00        NaN
0     4.063510 2022-04-02 09:00:00        NaN
0     4.858168 2022-04-02 10:00:00        NaN
0     4.035672 2022-04-02 11:00:00        NaN
0     6.640775 2022-04-02 12:00:00        NaN
0     6.699394 2022-04-02 13:00:00        NaN
0     5.591253 2022-04-02 14:00:00        NaN
0     2.823832 2022-04-02 15:00:00   2.823832
0          NaN 2022-04-02 16:00:00   0.881400
0     0.182158 2022-04-02 17:00:00   0.182158
0     0.128065 2022-04-03 06:00:00   0.091569
0     1.123854 2022-04-03 07:00:00   0.495897
0     1.691310 2022-04-03 08:00:00   0.482056
0     2.938999 2022-04-03 09:00:00   0.689978
0     3.465235 2022-04-03 10:00:00   0.679369
0     2.317206 2022-04-03 11:00:00   0.598739
0     4.631424 2022-04-03 12:00:00   0.612722
0     3.666460 2022-04-03 13:00:00   0.633525
0     3.100642 2022-04-03 14:00:00   0.610031
0     1.716756 2022-04-03 15:00:00   0.609681
0     0.234028 2022-04-03 16:00:00   0.234028

In [11]:
line_color = [
    '#1f77b4',  # muted blue
    '#ff7f0e',  # safety orange
    '#2ca02c',  # cooked asparagus green
    '#d62728',  # brick red
    '#9467bd',  # muted purple
    '#8c564b',  # chestnut brown
    '#e377c2',  # raspberry yogurt pink
    '#7f7f7f',  # middle gray
    '#bcbd22',  # curry yellow-green
    '#17becf'   # blue-teal
]


xtick = int(len(future_power['TIME_TO_INTERVAL'])/240)

fig_line = go.Figure()

fig_line.add_trace(go.Scatter(y = future_power['cloud_Power'], x=future_power['TIME_TO_INTERVAL'],
                    mode='lines',
                    name='真實值',
                    line={'dash': 'dash'},
                    line_color= '#1f77b4'))
fig_line.add_trace(go.Scatter(y = data['Power'], x=data['TIME_TO_INTERVAL'],
                    mode='lines',
                    name='真實值',
                    line={'dash': 'dash'},
                    line_color= '#ff7f0e'))
fig_line.update_layout(
    yaxis_title='發電量',
    xaxis_title='日期',
    title='彰師大汙水廠預測結果',
    font=dict(
        size=18,
    ),
#     yaxis2=dict(anchor='x', overlaying='y', side='right')
    height=450, 
    width=1500,

)

fig_line.update_xaxes(nticks=xtick)


#     fig_line.write_html(f'{folder_path}/img/{methods}_{i}.html')

fig_line.show()

In [12]:
future_power = future_power.fillna(0)
future_power.head(50)

cloud_Power    TIME_TO_INTERVAL  pre_Power
0     0.000000 2022-02-27 06:00:00   0.000000
0     0.000000 2022-02-27 07:00:00   0.000000
0     0.000000 2022-02-27 08:00:00   0.000000
0     0.000000 2022-02-27 09:00:00   0.000000
0     0.000000 2022-02-27 10:00:00   0.000000
0     0.000000 2022-02-27 11:00:00   0.000000
0     0.000000 2022-02-27 12:00:00   0.000000
0     0.000000 2022-02-27 13:00:00   0.000000
0     0.000000 2022-02-27 14:00:00   0.000000
0     0.000000 2022-02-27 15:00:00   0.000000
0     0.000000 2022-02-27 16:00:00   0.000000
0     0.000000 2022-02-27 17:00:00   0.000000
0     0.000000 2022-03-18 06:00:00   0.000000
0     0.000000 2022-03-18 07:00:00   0.000000
0     0.000000 2022-03-18 08:00:00   0.000000
0     5.605072 2022-03-18 09:00:00   0.000000
0     6.578561 2022-03-18 10:00:00   0.000000
0     0.000000 2022-03-18 11:00:00   0.000000
0     7.472419 2022-03-18 12:00:00   0.000000
0     0.000000 2022-03-18 13:00:00   0.000000
0     0.000000 2022-03-18 14:00:00   0.000000
0     0.000000 2022-03-18 15:00:00   0.000000
0     0.000000 2022-03-18 16:00:00   0.000000
0     0.000000 2022-03-18 17:00:00   0.000000
0     0.000000 2022-04-01 15:00:00   0.000000
0     0.000000 2022-04-01 16:00:00   0.000000
0     0.000000 2022-04-01 17:00:00   0.000000
0     0.164561 2022-04-02 06:00:00   0.000000
0     1.751811 2022-04-02 07:00:00   0.000000
0     2.900564 2022-04-02 08:00:00   0.000000
0     4.063510 2022-04-02 09:00:00   0.000000
0     4.858168 2022-04-02 10:00:00   0.000000
0     4.035672 2022-04-02 11:00:00   0.000000
0     6.640775 2022-04-02 12:00:00   0.000000
0     6.699394 2022-04-02 13:00:00   0.000000
0     5.591253 2022-04-02 14:00:00   0.000000
0     2.823832 2022-04-02 15:00:00   2.823832
0     0.000000 2022-04-02 16:00:00   0.881400
0     0.182158 2022-04-02 17:00:00   0.182158
0     0.128065 2022-04-03 06:00:00   0.091569
0     1.123854 2022-04-03 07:00:00   0.495897
0     1.691310 2022-04-03 08:00:00   0.482056
0     2.938999 2022-04-03 09:00:00   0.689978
0     3.465235 2022-04-03 10:00:00   0.679369
0     2.317206 2022-04-03 11:00:00   0.598739
0     4.631424 2022-04-03 12:00:00   0.612722
0     3.666460 2022-04-03 13:00:00   0.633525
0     3.100642 2022-04-03 14:00:00   0.610031
0     1.716756 2022-04-03 15:00:00   0.609681
0     0.234028 2022-04-03 16:00:00   0.234028

In [13]:
train = pd.merge(data,future_power,on = ['TIME_TO_INTERVAL'],how="inner")   

In [14]:
train

TIME_TO_INTERVAL       Date  Hour     Power      lon     lat  \
0    2022-02-27 06:00:00 2022-02-27     6  0.172272  120.425  23.325   
1    2022-02-27 07:00:00 2022-02-27     7  1.883819  120.725  23.625   
2    2022-02-27 08:00:00 2022-02-27     8  4.012042  121.025  23.925   
3    2022-02-27 09:00:00 2022-02-27     9  5.605072  121.325  24.225   
4    2022-02-27 10:00:00 2022-02-27    10  6.578561  121.625  24.525   
...                  ...        ...   ...       ...      ...     ...   
2175 2022-10-30 11:00:00 2022-10-30    11  4.761714  121.925  24.825   
2176 2022-10-30 12:00:00 2022-10-30    12  3.412161  122.225  25.125   
2177 2022-10-30 13:00:00 2022-10-30    13  4.729319  122.525  25.425   
2178 2022-10-30 14:00:00 2022-10-30    14  4.078483  122.825  25.725   
2179 2022-10-30 15:00:00 2022-10-30    15  2.323181      NaN  25.925   

         cloud       low  mid  hig  cloud_Power  pre_Power  
0     0.000000  0.000000  0.0  0.0          0.0   0.000000  
1     0.000000  0.000000  0.0  0.0          0.0   0.000000  
2     0.000000  0.000000  0.0  0.0          0.0   0.000000  
3     5.471000  5.471000  0.0  0.0          0.0   0.000000  
4     7.893267  7.893267  0.0  0.0          0.0   0.000000  
...        ...       ...  ...  ...          ...        ...  
2175  0.000000  0.000000  0.0  0.0          0.0   6.549119  
2176  0.000000  0.000000  0.0  0.0          0.0   6.413550  
2177  0.000000  0.000000  0.0  0.0          0.0   5.641947  
2178  0.000000  0.000000  0.0  0.0          0.0   3.924533  
2179  0.000000  0.000000  0.0  0.0          0.0   1.794878  

[2180 rows x 12 columns]

In [15]:
test_split_date = '2022-10-01'
test_split_date2 = '2022-10-31'
test_split_date = pd.to_datetime(test_split_date)
test_split_date2 = pd.to_datetime(test_split_date2)
train['TIME_TO_INTERVAL'] = pd.to_datetime(train['TIME_TO_INTERVAL'])
train['Date'] = train['TIME_TO_INTERVAL'].dt.date
mask_1 = (train['Date'] <= test_split_date)
train_data = train[mask_1].reset_index(drop=True)
print(len(train_data))
mask_2 = (train['Date'] <= test_split_date2)
test_data = train[~mask_1&mask_2].reset_index(drop=True)
print(len(test_data))
feature_data = ['pre_Power','cloud_Power']
train_x = train_data[feature_data]
train_y = train_data[['Power']]
test_x = test_data[feature_data]
test_y = test_data[['Power']]

scaler_x = MinMaxScaler()
scaler_x.fit(train_x[feature_data])
train_x = scaler_x.transform(train_x[feature_data])
test_x = scaler_x.transform(test_x[feature_data])
scaler_y = MinMaxScaler()
scaler_y.fit(train_y[['Power']])
train_y = scaler_y.transform(train_y[['Power']])

train_x, train_y = np.array(train_x), np.array(train_y)
test_x, test_y = np.array(test_x), np.array(test_y)
train_idx, test_idx = pd.DataFrame(), pd.DataFrame()  
pred = model_build(train_x, train_y, train_idx, test_x, test_y, test_idx, 'rvm')
pred['pred'] = pred['pred'].where(pred['pred'] >= 0, 0)

1839
341


C:\Users\GodZen\Anaconda3\envs\python3.6\lib\site-packages\sklearn\utils\validation.py:63: DataConversionWarning:

A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().



In [16]:
Baoshan = pd.read_csv(f'Plant_Info_Baoshan.csv', low_memory=False)
solar_capacity = Baoshan['Capacity'][1]
solar_capacity

9.7

In [17]:
print(round(MRE(pred['true'], pred['pred'],solar_capacity),2))
print(round(nRMSE(pred['true'], pred['pred']),2))
print(round(nMAE(pred['true'], pred['pred']),2))
print(round(RMSE(pred['true'], pred['pred']),2))
print(round(MAE(pred['true'], pred['pred']),2))

9.66
41.97
30.74
1.28
0.94


In [18]:
line_color = [
    '#1f77b4',  # muted blue
    '#ff7f0e',  # safety orange
    '#2ca02c',  # cooked asparagus green
    '#d62728',  # brick red
    '#9467bd',  # muted purple
    '#8c564b',  # chestnut brown
    '#e377c2',  # raspberry yogurt pink
    '#7f7f7f',  # middle gray
    '#bcbd22',  # curry yellow-green
    '#17becf'   # blue-teal
]


xtick = int(len(test_data['TIME_TO_INTERVAL'])/24)

fig_line = go.Figure()

fig_line.add_trace(go.Scatter(y = pred['true'], x=test_data['TIME_TO_INTERVAL'],
                    mode='lines',
                    name='真實值',
                    line={'dash': 'dash'},
                    line_color= '#1f77b4'))
fig_line.add_trace(go.Scatter(y = pred['pred'], x=test_data['TIME_TO_INTERVAL'],
                    mode='lines',
                    name='預測值',
                    line_color= '#ff7f0e'))
fig_line.update_layout(
    yaxis_title='發電量',
    xaxis_title='日期',
    title='彰師大汙水廠預測結果',
    font=dict(
        size=18,
    ),
#     yaxis2=dict(anchor='x', overlaying='y', side='right')
    height=450, 
    width=1500,

)

fig_line.update_xaxes(nticks=xtick)


#     fig_line.write_html(f'{folder_path}/img/{methods}_{i}.html')

fig_line.show()